## Quick Description

This notebook uses NVIDIA's NeMo library to segment YouTube subtitles with a BERT based model

In [1]:
import pandas as pd
import glob
import os
import yaml
from tqdm import tqdm

from nemo.collections.nlp.models import PunctuationCapitalizationModel

[NeMo W 2022-03-16 22:32:42 optimizers:55] Apex was not found. Using the lamb or fused_adam optimizer will error out.
[NeMo W 2022-03-16 22:32:43 __init__:22] `pynini` is not installed ! 
    Please run the `nemo_text_processing/setup.sh` script prior to usage of this toolkit.


In [2]:
filepaths = yaml.load(open("../config/filepaths.yaml"))

[NeMo W 2022-03-16 22:32:43 nemo_logging:349] /tmp/ipykernel_112569/1983981293.py:1: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
      filepaths = yaml.load(open("../config/filepaths.yaml"))
    


In [3]:
model = PunctuationCapitalizationModel.from_pretrained("punctuation_en_bert")

[NeMo I 2022-03-16 22:32:43 cloud:56] Found existing object /home/guilherme/.cache/torch/NeMo/NeMo_1.8.0rc0/punctuation_en_bert/93b0369b5e0d147f61895feffcbcfb88/punctuation_en_bert.nemo.
[NeMo I 2022-03-16 22:32:43 cloud:62] Re-using file from: /home/guilherme/.cache/torch/NeMo/NeMo_1.8.0rc0/punctuation_en_bert/93b0369b5e0d147f61895feffcbcfb88/punctuation_en_bert.nemo
[NeMo I 2022-03-16 22:32:43 common:704] Instantiating model from pre-trained checkpoint
[NeMo I 2022-03-16 22:32:52 tokenizer_utils:125] Getting HuggingFace AutoTokenizer with pretrained_model_name: bert-base-uncased, vocab_file: /tmp/tmpmbc1vsw8/tokenizer.vocab_file, special_tokens_dict: {}, and use_fast: False


Using eos_token, but it is not set yet.
Using bos_token, but it is not set yet.
[NeMo W 2022-03-16 22:32:58 modelPT:148] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    use_tarred_dataset: false
    label_info_save_dir: null
    text_file: text_train.txt
    labels_file: labels_train.txt
    tokens_in_batch: null
    max_seq_length: 128
    num_samples: -1
    use_cache: true
    cache_dir: null
    get_label_frequences: false
    verbose: true
    n_jobs: 0
    tar_metadata_file: null
    tar_shuffle_n: 1
    shuffle: true
    drop_last: false
    pin_memory: true
    num_workers: 8
    persistent_workers: true
    ds_item: punct_dataset_complete
    
[NeMo W 2022-03-16 22:32:58 modelPT:155] If you intend to do validation, please call the ModelPT.setup_validation_data() or ModelPT.setup_multiple_validation_data() method and provide a valid co

[NeMo I 2022-03-16 22:33:03 save_restore_connector:157] Model PunctuationCapitalizationModel was successfully restored from /home/guilherme/.cache/torch/NeMo/NeMo_1.8.0rc0/punctuation_en_bert/93b0369b5e0d147f61895feffcbcfb88/punctuation_en_bert.nemo.


In [4]:
filenames = [file.split("/")[-1] for file in glob.glob(os.path.join(filepaths["preprocessed_data"], "*"))]

for filename in tqdm(filenames, total=len(filenames)):
    with open(os.path.join(filepaths["preprocessed_data"], filename)) as file:
        text = file.read()
        
    text = model.add_punctuation_capitalization([text])[0]
    text = text.split('.')
    text = [s.strip() for s in text]

    df = pd.DataFrame(text, columns=["text"])
    # Remove evetual splits on the final period
    df = df[df.text != '']
    df.to_csv(os.path.join(filepaths["model_based_segmentated_data"], filename), index=False)

  0%|                                                                         | 0/552 [00:00<?, ?it/s]

[NeMo I 2022-03-16 22:33:03 punctuation_capitalization_model:1068] Using batch size 1 for inference
[NeMo I 2022-03-16 22:33:03 punctuation_capitalization_infer_dataset:91] Max length: 64
[NeMo I 2022-03-16 22:33:03 data_preprocessing:358] Some stats of the lengths of the sequences:
[NeMo I 2022-03-16 22:33:03 data_preprocessing:360] Min: 2409 |                  Max: 2409 |                  Mean: 2409.0 |                  Median: 2409.0
[NeMo I 2022-03-16 22:33:03 data_preprocessing:366] 75 percentile: 2409.00
[NeMo I 2022-03-16 22:33:03 data_preprocessing:367] 99 percentile: 2409.00



 33%|████████████████████▎                                        | 98/295 [00:10<00:20,  9.81batch/s]


 66%|███████████████████████████████████████▊                    | 196/295 [00:21<00:09, 10.16batch/s]


  0%|                                                               | 1/552 [00:31<4:49:46, 31.56s/it]

...


 78%|██████████████████████████████████████████████▉             | 154/197 [00:09<00:02, 14.90batch/s]


100%|████████████████████████████████████████████████████████████▉| 551/552 [2:00:24<00:18, 18.12s/it]

[NeMo I 2022-03-17 00:33:28 punctuation_capitalization_model:1068] Using batch size 1 for inference
[NeMo I 2022-03-17 00:33:28 punctuation_capitalization_infer_dataset:91] Max length: 64
[NeMo I 2022-03-17 00:33:28 data_preprocessing:358] Some stats of the lengths of the sequences:
[NeMo I 2022-03-17 00:33:28 data_preprocessing:360] Min: 1433 |                  Max: 1433 |                  Mean: 1433.0 |                  Median: 1433.0
[NeMo I 2022-03-17 00:33:28 data_preprocessing:366] 75 percentile: 1433.00
[NeMo I 2022-03-17 00:33:28 data_preprocessing:367] 99 percentile: 1433.00



 88%|████████████████████████████████████████████████████▋       | 152/173 [00:09<00:01, 14.05batch/s]


100%|█████████████████████████████████████████████████████████████| 552/552 [2:00:35<00:00, 13.11s/it]
